# Loading Packages

In [1]:
import numpy as np
import pandas as pd
import nltk
import keras

Using TensorFlow backend.


In [0]:
from keras.models import Sequential, Model
from keras.layers import Dense, Activation, LSTM, Embedding, InputLayer, Bidirectional, TimeDistributed, Input, Concatenate, Reshape, Lambda, Flatten, RepeatVector, Dot
from keras.utils import to_categorical
from keras.optimizers import Adam
from keras import backend as K
import tensorflow as tf

# Loading Data

In [0]:
'''
The files new_train.nl has the paraphrased data set and the file new_train.sql has the corresponding SQL queries for the paraphrased inputs
'''

ftrain_x = open('new_train.nl').read().split('\n')
ftrain_y = open('new_train.sql').read().split('\n')
ftest_x = open('test.nl').read().split('\n')
ftest_y = open('test.sql').read().split('\n')


# ftrain_x = open('train_en.txt').read().split('\n')
# ftrain_y = open('train_ja.txt').read().split('\n')
# ftest_x = open('test_en.txt').read().split('\n')
# ftest_y = open('test_ja.txt').read().split('\n')

In [0]:
# print(len(ftrain_x), len(ftrain_y))
'''
Here we are subsetting or training dataset to only consider records that has a maximum of 50 words in SQL output
'''

train_x = []
train_y = []
test_x = []
test_y = []

for i in range(len(ftrain_y)):
  if len(ftrain_y[i].split()) <= 50:
    train_x.append(ftrain_x[i])
    train_y.append(ftrain_y[i])
  
# print(len(train_x), len(train_y))

for i in range(len(ftest_y)):
  if len(ftest_y[i].split()) <= 50:
    test_x.append(ftest_x[i])
    test_y.append(ftest_y[i])

# Creating Index for NL Data

In [0]:
'''
Creating unique index for every tokens in training data natural language file.
Here we are adding unique indices for <PAD> and <UNK>
'''

train_corpus_nl = set([word for each in train_x for word in each.split()])

idx2word_nl = {idx + 2 : word for idx, word in enumerate(train_corpus_nl)}
idx2word_nl[0] = '<PAD>'
idx2word_nl[1] = '<UNK>'

word2idx_nl = {word : idx + 2 for idx, word in enumerate(train_corpus_nl)}
word2idx_nl['<PAD>'] = 0
word2idx_nl['<UNK>'] = 1

len_x = len(idx2word_nl)

In [0]:
words_x =  [[word for word in each.split()] for each in train_x]

words_x_idx = [[word2idx_nl[word] for word in each] for each in words_x ]

# Creating Index for SQL Data

In [0]:
'''
Creating unique index for every tokens in training data SQL file.
Here we are adding unique indices for special tags <PAD>, <UNK>, <SOS>, <EOS>
'''

train_corpus_sql = set([word for each in train_y for word in each.split()])

idx2word_sql = {idx + 4 : word for idx, word in enumerate(train_corpus_sql)}
idx2word_sql[0] = '<PAD>'
idx2word_sql[1] = '<UNK>'
idx2word_sql[2] = '<SOS>'
idx2word_sql[3] = '<EOS>'

word2idx_sql = {word : idx + 4for idx, word in enumerate(train_corpus_sql)}
word2idx_sql['<PAD>'] = 0
word2idx_sql['<UNK>'] = 1
word2idx_sql['<SOS>'] = 2
word2idx_sql['<EOS>'] = 3

len_y = len(idx2word_sql)

In [0]:
words_y =  [['<SOS>'] + [word for word in each.split()] + ['<EOS>'] for each in train_y]

words_y_idx = [[word2idx_sql[word] for word in each] for each in words_y ]

words_target = [[word for word in each.split()] + ['<EOS>'] for each in train_y]

words_target_idx = [[word2idx_sql[word] for word in each] for each in words_target ]

In [9]:
max_x = max([len(each) for each in words_x_idx])
max_y = max([len(each) for each in words_y_idx])



print(max_x)
print(max_y)
print(len_x)
print(len_y)

23
52
733
388


In [0]:
words_x_idx_pad = [each + [0] * (max_x - len(each)) for each in words_x_idx]
words_y_idx_pad = [each + [0] * (max_y - len(each)) for each in words_y_idx]
words_target_idx_pad = [each + [0] * (max_y - len(each)) for each in words_target_idx]

In [0]:
words_x_idx_enc = []

for each in words_x_idx_pad:
  each_array = []
  for idx in each:
    temp = [0] * len_x
    temp[idx] = 1
    each_array.append(temp)
  words_x_idx_enc.append(each_array)
  

words_y_idx_enc = []

for each in words_y_idx_pad:
  each_array = []
  for idx in each:
    temp = [0] * len_y
    temp[idx] = 1
    each_array.append(temp)
  words_y_idx_enc.append(each_array)

In [0]:
words_target_idx_enc = []

for each in words_target_idx_pad:
  each_array = []
  for idx in each:
      temp = [0] * len_y
      temp[idx] = 1
      each_array.append(temp)
  words_target_idx_enc.append(each_array)

# words_target_idx_arr = np.zeros((len(train_y), max_y, len_y))

#words_target_idx_arr = [[np.zeros((len_y))[idx] = 1 for idx in each] for each in words_target_idx_pad]

In [13]:
print(len(words_target_idx_enc[0][0]))

388


In [0]:
words_x_idx_arr = np.array(words_x_idx_enc)
words_x_idx_enc = []

words_y_idx_arr = np.array(words_y_idx_enc)
words_y_idx_enc = []

words_target_idx_arr = np.array(words_target_idx_enc)
words_target_idx_enc = []

In [15]:
#words_x_idx_arr = words_x_idx_arr.reshape(-1, 1, max_x)
#words_y_idx_arr = words_y_idx_arr.reshape(-1, 1, max_y)
#words_target_idx_arr = words_target_idx_arr.reshape(-1, 1, max_y)
print(words_x_idx_arr.shape)
print(words_y_idx_arr.shape)
print(words_target_idx_arr.shape)

(9439, 23, 733)
(9439, 52, 388)
(9439, 52, 388)


# Encoder Model

In [0]:
# enInput = Input(shape = (None,max_x))
# print(enInput.shape)
# #enInput2 = tf.reshape(enInput, [-1, max_x])
# #enReshape= Reshape((max_x))
# #enInput2 = enReshape(enInput)
# enInput2 = Lambda(lambda x: x[:, max_x])(enInput)
# print(enInput2.shape)
# enEmbed = Embedding(input_dim = len(idx2word_nl), output_dim = 300)
# enEmbedOutput = enEmbed(enInput2)
# print(enEmbedOutput.shape)
# enLSTM = LSTM(256, return_state = True)
# enOutput, enHiddenState, enCellState = enLSTM(enEmbedOutput)
# enFinal = [enHiddenState, enCellState]

In [17]:
'''
Encoder model has a LSTM layer with 64 units or cells. Here we should return only the final state, hence
return_sequences = False and we set return_state = True for the cell states. The final output of encoder is 
final hidden state and cell state are concatenated.
'''

enInput = Input(shape = (None,len_x))
#print(enInput.shape)
#enInput2 = tf.reshape(enInput, [-1, max_x])
#enReshape= Reshape((max_x))
#enInput2 = enReshape(enInput)
#enInput2 = Lambda(lambda x: x[:, max_x])(enInput)
#print(enInput2.shape)
# enEmbed = Embedding(input_dim = len_x, output_dim = 300, input_shape = (None,len_x))
# enEmbedOutput = enEmbed(enInput)
# print(enEmbedOutput.shape)
# enReshape= Reshape((max_x, 300))
# enInput2 = enReshape(enEmbedOutput)
# print(enInput2.shape)
enLSTM = LSTM(64, return_state = True, return_sequences = False)
enOutput, enHiddenState, enCellState = enLSTM(enInput)
enFinal = [enHiddenState, enCellState]

Instructions for updating:
Colocations handled automatically by placer.


In [18]:
print(enCellState.shape)

(?, 64)


# Decoder Model 

In [0]:
# deInput = Input(shape = (None, max_y))
# print(deInput.shape)
# #deInput2 = tf.reshape(deInput, [-1, max_y])
# deInput2 = Lambda(lambda x: x[:, max_y])(deInput)
# print(deInput2.shape)
# deEmbed = Embedding(input_dim = len(idx2word_sql), output_dim = 300)
# deEmbedOutput = deEmbed(deInput2)
# print(deEmbedOutput.shape)
# deLSTM = LSTM(256, return_sequences = True, return_state = True)
# deOutput, deHiddenState, deCellState = deLSTM(deEmbedOutput, initial_state = enFinal)
# print(deOutput.shape)
# deFlatten = Flatten()
# deFlattenOutput = deFlatten(deOutput)
# print(deFlattenOutput.shape)
# deDense = Dense(max_y, activation = 'softmax')
# deDenseOutput = deDense(deFlattenOutput)
# print(deDenseOutput.shape)

In [20]:
'''
Decoder model has a LSTM layer with 64 units or cells. Here we should return a sequence, hence
return_sequences = True and we set return_state = True for the cell states. 
'''

deInput = Input(shape = (None, len_y))
print(deInput.shape)
#deInput2 = tf.reshape(deInput, [-1, max_y])
#deInput2 = Lambda(lambda x: x[:, max_y])(deInput)
print(deInput.shape)
# deEmbed = Embedding(input_dim = len(idx2word_sql), output_dim = 300, input_shape = (None, len_y))
# deEmbedOutput = deEmbed(deInput)
# print(deEmbedOutput.shape)
# deReshape = Reshape((max_y, 300))
# deInput2 = deReshape(deEmbedOutput)
# print(deInput2.shape)
deLSTM = LSTM(64, return_sequences = True, return_state = True)
deOutput, deHiddenState, deCellState = deLSTM(deInput, initial_state = enFinal)
print(deOutput.shape)
#deFlatten = Flatten()
#deFlattenOutput = deFlatten(deOutput)
#print(deFlattenOutput.shape)
deDense = Dense(len_y, activation = 'softmax')
deDenseOutput = deDense(deOutput)
print(deDenseOutput.shape)

(?, ?, 388)
(?, ?, 388)
(?, ?, 64)
(?, ?, 388)


In [21]:
model = Model(inputs = [enInput, deInput], outputs = [deDenseOutput])
model.summary()

__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_1 (InputLayer)            (None, None, 733)    0                                            
__________________________________________________________________________________________________
input_2 (InputLayer)            (None, None, 388)    0                                            
__________________________________________________________________________________________________
lstm_1 (LSTM)                   [(None, 64), (None,  204288      input_1[0][0]                    
__________________________________________________________________________________________________
lstm_2 (LSTM)                   [(None, None, 64), ( 115968      input_2[0][0]                    
                                                                 lstm_1[0][1]                     
          

In [22]:
model.compile(optimizer = Adam(0.1), loss = 'categorical_crossentropy', metrics = ['accuracy'])
model.fit(x = [words_x_idx_arr, words_y_idx_arr], y = words_target_idx_arr, batch_size = 64, validation_split = 0.2, epochs = 20, verbose = 1, shuffle = True)

Instructions for updating:
Use tf.cast instead.
Instructions for updating:
Deprecated in favor of operator or tf.math.divide.
Train on 7551 samples, validate on 1888 samples
Epoch 1/20
7551/7551 [==============================] - 34s 4ms/step - loss: 1.4030 - acc: 0.6965 - val_loss: 0.5533 - val_acc: 0.8880
Epoch 2/20
7551/7551 [==============================] - 32s 4ms/step - loss: 0.4053 - acc: 0.9115 - val_loss: 0.4337 - val_acc: 0.9038
Epoch 3/20
7551/7551 [==============================] - 31s 4ms/step - loss: 0.3445 - acc: 0.9209 - val_loss: 0.4254 - val_acc: 0.9063
Epoch 4/20
7551/7551 [==============================] - 31s 4ms/step - loss: 0.3289 - acc: 0.9236 - val_loss: 0.4213 - val_acc: 0.9109
Epoch 5/20
7551/7551 [==============================] - 31s 4ms/step - loss: 0.3177 - acc: 0.9256 - val_loss: 0.4105 - val_acc: 0.9157
Epoch 6/20
7551/7551 [==============================] - 31s 4ms/step - loss: 0.3043 - acc: 0.9301 - val_loss: 0.4763 - val_acc: 0.8916
Epoch 7/20
7551/

# Inference Models

In [0]:
enInfModel = Model(inputs = enInput, outputs = enFinal)

In [24]:
print(deInput.shape)

(?, ?, 388)


In [25]:
deInfInput = deInput
print(deInfInput.shape)
# deInfInput2 = deReshape(deInfInput)
# print(deInfInput2.shape)
deInfHiddenInput = Input(shape = (64,))
print(deInfHiddenInput.shape)


deInfCellInput = Input(shape = (64,))
print(deInfCellInput.shape)
deInfOutput, deInfHiddenOutput, deInfCellOutput = deLSTM(deInfInput, initial_state = [deInfHiddenInput, deInfCellInput])
deInfOutput2 = deDense(deInfOutput)
print(deInfOutput2.shape)

deInfModel = Model(inputs = [deInput] + [deInfHiddenInput, deInfCellInput], outputs = [deInfOutput2] + [deInfHiddenOutput, deInfCellOutput])

(?, ?, 388)
(?, 64)
(?, 64)
(?, ?, 388)


# Test Data

In [0]:
test_words_x =  [[word for word in each.split()] for each in test_x]

test_words_x_idx = [[word2idx_nl[word] if word in word2idx_nl.keys() else 1 for word in each][0:max_x] for each in test_words_x ]



In [0]:
'''
Converting the tokens in text data to index and if a new word is encountered we are replacing it with 1 which is the index for <UNK>
'''

test_words_y =  [['<SOS>'] + [word for word in each.split()] + ['<EOS>'] for each in test_y]

test_words_y_idx = [[word2idx_sql[word] if word in word2idx_sql.keys() else 1 for word in each] for each in test_words_y ]

test_words_target = [[word for word in each.split()] + ['<EOS>'] for each in test_y]

test_words_target_idx = [[word2idx_sql[word] if word in word2idx_sql.keys() else 1 for word in each] for each in test_words_target ]

In [0]:
test_words_x_idx_pad = [each + [0] * (max_x - len(each)) for each in test_words_x_idx]
test_words_y_idx_pad = [each + [0] * (max_y - len(each)) for each in test_words_y_idx]
test_words_target_idx_pad = [each + [0] * (max_y - len(each)) for each in test_words_target_idx]

In [0]:
test_words_x_idx_enc = []

for each in test_words_x_idx_pad:
  each_array = []
  for idx in each:
    temp = [0] * len_x
    temp[idx] = 1
    each_array.append(temp)
  test_words_x_idx_enc.append(each_array)


test_words_y_idx_enc = []

for each in test_words_y_idx_pad:
  each_array = []
  for idx in each:
    temp = [0] * len_y
    temp[idx] = 1
    each_array.append(temp)
  test_words_y_idx_enc.append(each_array)

In [0]:
test_words_target_idx_enc = []

for each in test_words_target_idx_pad:
  each_array = []
  for idx in each:
      temp = [0] * len_y
      temp[idx] = 1
      each_array.append(temp)
  test_words_target_idx_enc.append(each_array)

In [0]:
test_words_x_idx_arr = np.array(test_words_x_idx_enc)
test_words_x_idx_enc = []

test_words_y_idx_arr = np.array(test_words_y_idx_enc)
test_words_y_idx_enc = []

test_words_target_idx_arr = np.array(test_words_target_idx_enc)
test_words_target_idx_enc = []

In [32]:
print(test_words_x_idx_arr.shape)
print(test_words_y_idx_arr.shape)
print(test_words_target_idx_arr.shape)


(186, 23, 733)
(186, 52, 388)
(186, 52, 388)


In [0]:
# test_words_x_idx_arr = test_words_x_idx_arr.reshape(-1, 1, max_x)
# test_words_y_idx_arr = test_words_y_idx_arr.reshape(-1, 1, max_y)

In [34]:
model.evaluate(x = [test_words_x_idx_arr, test_words_y_idx_arr], y = test_words_target_idx_arr)

186/186 [==============================] - 0s 2ms/step


[6.163202070420788, 0.49172869901503286]

In [35]:
accuracy = model.evaluate(x = [test_words_x_idx_arr, test_words_y_idx_arr], y = test_words_target_idx_arr)[1]* 100
print("The test accuracy of Encode-Decoder Model is {}".format(round(accuracy, 2)))

186/186 [==============================] - 0s 1ms/step
The test accuracy of Encode-Decoder Model is 49.17


In [36]:
print(test_words_x_idx_arr.shape)
print(test_words_y_idx_arr.shape)

for i in range(test_words_x_idx_arr.shape[0]):
  output = model.predict([test_words_x_idx_arr[i].reshape(1, max_x, len_x), test_words_y_idx_arr[i].reshape(1, max_y, len_y)])
  idx_array = []
  for each in output[0]:
    idx_array.append(np.argmax(each))
  query_array = [idx2word_sql[each] for each in idx_array]
  print(query_array)
  

(186, 23, 733)
(186, 52, 388)
['SELECT', 'DISTINCT', 'flight_1.flight_id', 'flight_1', 'fare', 'flight_1', 'flight_1.airline_code', 'flight_1.to_airport', 'WHERE', 'city', 'SELECT', 'MAX', 'flight_1', 'flight', 'airport_service_2', 'airport_service_1', 'flight_fare', 'airline_1.airline_code', 'flight_1.to_airport', 'MAX', '(', 'flight', '=', '=', 'flight_1.airline_code', 'flight_1.airline_code', 'AND', 'fare_basis_1.fare_basis_code', 'flight_1.flight_days', '=', '<EOS>', 'flight_1.arrival_time', '=', '0', "COUNTY'", 'flight_1.departure_time', '=', 'airport_service_2.airport_code', '=', 'flight_1.to_airport', "PAUL'", '<PAD>', "COUNTY'", '<', 'flight_1.flight_days', '=', "'CP'", 'AND', '=', '<EOS>', '<PAD>', '<PAD>']
['SELECT', 'DISTINCT', 'flight_1.flight_id', 'flight_1', 'fare', 'ground_service_1', 'flight_1.from_airport', 'flight', '=', 'aircraft_1.capacity', 'MAX', 'MAX', 'flight', 'city_2', 'flight_1.airline_code', ',', 'airport_service', '<EOS>', 'FROM', '<PAD>', '<PAD>', '<PAD>',

In [0]:
print(words_x_idx_arr.shape)
print(words_y_idx_arr.shape)

for i in range(words_x_idx_arr.shape[0]):
  output = model.predict([words_x_idx_arr[i].reshape(1, max_x, len_x), words_y_idx_arr[i].reshape(1, max_y, len_y)])
  idx_array = []
  for each in output[0]:
    idx_array.append(np.argmax(each))
  query_array = [idx2word_sql[each] for each in idx_array]
  print(query_array)

(8512, 23, 715)
(8512, 51, 381)
['SELECT', 'DISTINCT', 'flight_1.flight_id', 'FROM', 'flight', 'flight_1', ',', 'airport_service', 'airport_1', ',', 'airport', 'airport_service_1', ',', 'city', 'city_1', 'WHERE', 'airport_1.airport_code', '=', 'airport_1.airport_code', 'AND', 'airport_1.airport_code', '=', "'MKE'", 'AND', 'flight_1.from_airport', '=', 'airport_service_1.airport_code', 'AND', 'airport_service_1.city_code', '=', 'city_1.city_code', 'AND', '1', '=', '1', '<EOS>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>']
['SELECT', 'DISTINCT', 'flight_1.flight_id', 'FROM', 'flight', 'flight_1', ',', 'airport', 'airport_1', ',', 'airport', 'airport_service_1', ',', 'city', 'city_1', 'WHERE', 'flight_1.airline_code', '=', 'airport_1.airport_code', 'AND', 'airport_1.airport_code', '=', "'MKE'", 'AND', 'flight_1.from_airport', '=', 'airport_service_1.airport_code', 'AND', 'airport_service_1.city_code'

In [37]:
'''
Encoder-Decoder Model creates SQL like sentences
'''

for i in range(5):
  x = test_words_x_idx_arr[i].reshape(1, max_x, len_x)
  #print(x)
  y = test_words_y_idx_arr[i].reshape(1, max_y, len_y)
  en_states = enInfModel.predict(x)
  #print(en_states)
  sample_y = np.zeros((1, 1, len_y))
  #print(sample_y.shape)
  sample_y[0, 0, word2idx_sql['<SOS>']] = 1
  #sample_y[0, 0, 0] = word2idx_sql['<SOS>']
  flag = False
  pos = 0
  final_query = []
  while not flag:
    #sample_y_arr = np.array([sample_y]).reshape(1, 1, 1)
    #print(sample_y_arr.shape)
#     print(en_states[0].shape)
#     print(pos)
    de_output, de_hidden, de_cell = deInfModel.predict([sample_y] + en_states)
    #print(de_output.shape)
    idx = np.argmax(de_output[0][0])
#     print(idx)
    query = idx2word_sql[idx]
    #print(query_array)
    final_query.append(query)
    
    
    if query == '<EOS>' or pos > 99:
      flag = True
      break
    
    pos += 1
    sample_y = np.zeros((1, 1, len_y))
    sample_y[0, 0, idx] = 1
    en_states = [de_hidden, de_cell]
  
  #print([idx2word_sql[each] for each in test_words_x_idx_arr[i][0]])
  print(' '.join([idx2word_sql[np.argmax(each)] for each in test_words_y_idx_arr[i]]))
  print(' '.join(final_query))   
  print('\n')
  


<SOS> SELECT DISTINCT <UNK> FROM flight WHERE ( <UNK> <UNK> ( SELECT <UNK> FROM airport_service WHERE <UNK> <UNK> ( SELECT <UNK> FROM city WHERE <UNK> = 'DALLAS' <UNK> AND <UNK> <UNK> ( SELECT <UNK> FROM airport_service WHERE <UNK> <UNK> ( SELECT <UNK> FROM city WHERE <UNK> = 'PHOENIX' <UNK> ) <EOS> <PAD>
SELECT DISTINCT flight_1.flight_id FROM flight flight_1 , airport_service airport_service_1 , city city_1 , airport_service airport_service_2 , city city_2 WHERE flight_1.from_airport = airport_service_1.airport_code AND airport_service_1.city_code = city_1.city_code AND city_1.city_name = 'DENVER' AND flight_1.to_airport = airport_service_2.airport_code AND airport_service_2.city_code = city_2.city_code AND city_2.city_name = 'PITTSBURGH' AND flight_1.arrival_time < 1000 ) <EOS>


<SOS> SELECT DISTINCT <UNK> FROM ground_service WHERE <UNK> <UNK> ( SELECT <UNK> FROM city WHERE <UNK> = 'DENVER' ) <EOS> <PAD> <PAD> <PAD> <PAD> <PAD> <PAD> <PAD> <PAD> <PAD> <PAD> <PAD> <PAD> <PAD> <PAD> 

In [0]:
#x = Input(shape = (None,))
#softmax = keras.activations.softmax(x, axis = 1)

# Attention Model

In [0]:
'''
The attention unit takes as input the encoder activations and returns the context as ouput
'''
def attentionUnit(a, h_prev):

    atRepeat = RepeatVector(max_x)
    
    h_prev = atRepeat(h_prev)
    
    
    atConcat = Concatenate(axis = -1)
    
    concat = atConcat([a, h_prev])

    
    atDense1 = Dense(20, activation = 'tanh')
    
    dense1 = atDense1(concat)
    
    
    atDense2 = Dense(1, activation = 'relu')
    
    dense2 = atDense2(dense1)
    
    
    alphas = keras.layers.Softmax(axis = 1)(dense2)
    
    
    atDot = Dot(axes = 1)
    
    context = atDot([alphas, a])

    return context

In [0]:
n_a = 64
n_h = 64

h0 = np.zeros((len(train_x), n_h))
c0 = np.zeros((len(train_x), n_h))

postAttentionLSTMCell = LSTM(n_h, return_state = True)

words_target_idx_arr_swapped = list(words_target_idx_arr.swapaxes(0,1))

output_layer = Dense(len_y, activation='softmax')

In [0]:
'''
The model has an encoder LSTM layer or also called PreAttentionLSTM cell and a decoder LSTM layer called PostAttentionLSTM cell
'''

def model(Tx, Ty, n_a, n_h, len_x, len_y):


    X = Input(shape=(Tx, len_x))
    Y = Input(shape=(Ty, len_x))
    h0 = Input(shape=(n_h,))
    c0 = Input(shape=(n_h,))
    
    
    outputs = []
    

    preAttentionLSTMCell = Bidirectional(LSTM(n_a, return_sequences=True))
    
    a = preAttentionLSTMCell(X)

    h = h0
    c = c0

    for t in range(Ty):
      
#         atRepeat = RepeatVector(max_x)
    
#         h = atRepeat(h)
    
    
#         atConcat = Concatenate(axis = -1)
    
#         concat = atConcat([a, h])

    
#         atDense1 = Dense(20, activation = 'tanh')
    
#         dense1 = atDense1(concat)
    
    
#         atDense2 = Dense(1, activation = 'relu')
    
#         dense2 = atDense2(dense1)
    
    
#         alphas = keras.layers.Softmax(axis = 1)(dense2)
    
    
#         atDot = Dot(axes = 1)
    
#         context = atDot([alphas, a])
    

        context = attentionUnit(a, h)

        h, _, c = postAttentionLSTMCell(context, initial_state =  [h, c])
        
        out = output_layer(h)

        outputs.append(out)
    

    model = Model(inputs = [X, h0, c0], outputs = outputs)

    return model

In [0]:
attmodel = model(max_x, max_y, n_a, n_h, len_x, len_y)

In [0]:
words_y_idx_arr = np.zeros((1, 1))

In [0]:
attmodel.compile(optimizer = Adam(0.1), loss = 'categorical_crossentropy', metrics = ['accuracy'])


In [63]:

attmodel.fit([words_x_idx_arr, h0, c0], words_target_idx_arr_swapped, epochs = 10, batch_size = 64)

Epoch 1/10
9439/9439 [==============================] - 138s 15ms/step - loss: 173.0120 - dense_3_loss: 1.4728 - dense_3_acc: 0.8780 - dense_3_acc_1: 0.2780 - dense_3_acc_2: 0.0000e+00 - dense_3_acc_3: 0.0000e+00 - dense_3_acc_4: 0.0000e+00 - dense_3_acc_5: 0.0000e+00 - dense_3_acc_6: 0.0000e+00 - dense_3_acc_7: 0.0000e+00 - dense_3_acc_8: 0.0000e+00 - dense_3_acc_9: 0.0000e+00 - dense_3_acc_10: 0.0000e+00 - dense_3_acc_11: 0.0790 - dense_3_acc_12: 0.0790 - dense_3_acc_13: 0.0810 - dense_3_acc_14: 0.0808 - dense_3_acc_15: 0.0889 - dense_3_acc_16: 0.0898 - dense_3_acc_17: 0.0901 - dense_3_acc_18: 0.1331 - dense_3_acc_19: 0.1411 - dense_3_acc_20: 0.1421 - dense_3_acc_21: 0.1422 - dense_3_acc_22: 0.1483 - dense_3_acc_23: 0.1485 - dense_3_acc_24: 0.1535 - dense_3_acc_25: 0.1726 - dense_3_acc_26: 0.1751 - dense_3_acc_27: 0.1743 - dense_3_acc_28: 0.1740 - dense_3_acc_29: 0.2271 - dense_3_acc_30: 0.2337 - dense_3_acc_31: 0.2354 - dense_3_acc_32: 0.2461 - dense_3_acc_33: 0.2563 - dense_3_acc_3

In [0]:
pred = attmodel.predict([test_words_x_idx_arr, h0, c0])

In [65]:
print(test_words_x_idx_arr.shape)

output = []
for i in range(len(pred)):
  output.append([idx2word_sql[np.argmax(each)] for each in pred[i]])

(186, 23, 733)


In [68]:
output_array = np.transpose(np.array(output))
print(output_array.shape)

#for each in output_array:
  #print(' '.join(each))

(186, 52)


In [0]:
for each in output_array[:5]:
  word_array = []
  for word in each:
    if word != '<PAD>':
      word_array.append(word)
  print(' '.join(word_array))

SELECT DISTINCT flight_1.flight_id FROM flight flight_1 , city airport_service_1 , city airport_service_1 , airport_service airport_service_2 , city city_2 WHERE flight_1.from_airport = AND AND airport_service_1.city_code = = = = = ) AND AND = = AND AND = )
SELECT DISTINCT flight_1.flight_id FROM flight airline_1 ,
SELECT DISTINCT flight_1.flight_id FROM flight flight_1 , ground_service_1.city_code ground_service_1.city_code
SELECT DISTINCT flight_1.flight_id FROM flight flight_1 , city airport_service_1 , city city_1 , airport_service airport_service_2 , city city_2 WHERE flight_1.from_airport = airport_service_1.airport_code AND airport_service_1.city_code = = = = = = AND AND = = AND AND = = city_2.city_name city_2.city_name
SELECT DISTINCT flight_1.flight_id FROM flight flight_1 , city airport_service_1 , city city_1 , airport_service airport_service_2 , city city_2 WHERE flight_1.from_airport = airport_service_1.airport_code AND airport_service_1.city_code = = = = = = AND AND = = A